In [1]:
import pandas as pd
from IPython.display import display
import re
import numpy as np
from IPython.display import Image
import folium
from folium import plugins
from collections import Counter
import requests
import json
from config import gkey
from pprint import pprint
%matplotlib inline

In [2]:
# Convert to pandas DataFrame
results_df = pd.read_csv("../Resources/Accidental_Drug_Related_Deaths_2012-2017_cleaned.csv")

In [3]:
results_df.head()

CaseNumber        Date  Year   Sex   Race   Age Residence City  \
0   12-16897  11/30/2012  2012  Male  White  45.0            NaN   
1   13-11849   8/12/2013  2013  Male  White  30.0      NEW HAVEN   
2   14-17578  11/23/2014  2014  Male  White  27.0      NAUGATUCK   
3   12-11497   8/14/2012  2012  Male  White  21.0        ENFIELD   
4    13-2133    2/4/2013  2013  Male  White  25.0        POMFRET   

  Residence State Residence County   Death City     ...      Tramad  \
0             NaN              NaN    NEW HAVEN     ...         NaN   
1             NaN              NaN    NEW HAVEN     ...         NaN   
2             NaN              NaN  NEW MILFORD     ...         NaN   
3             NaN              NaN      ENFIELD     ...         NaN   
4             NaN          WINDHAM      POMFRET     ...         NaN   

  Morphine (not heroin) Other Any Opioid MannerofDeath AmendedMannerofDeath  \
0                   NaN   NaN        NaN      Accident                  NaN   
1                   NaN   NaN        NaN      Accident                  NaN   
2                   NaN   NaN        NaN      Accident                  NaN   
3                   NaN   NaN        NaN      Accident                  NaN   
4                   NaN   NaN        NaN      Accident                  NaN   

                                   DeathLoc DeathLocationCity DeathLocLat  \
0    NEW HAVEN, CT\n(41.308252, -72.924161)         NEW HAVEN    41.30825   
1    NEW HAVEN, CT\n(41.308252, -72.924161)         NEW HAVEN    41.30825   
2  NEW MILFORD, CT\n(41.576633, -73.408713)       NEW MILFORD    41.57663   
3      ENFIELD, CT\n(41.976501, -72.591985)           ENFIELD     41.9765   
4      POMFRET, CT\n(41.897524, -71.962064)           POMFRET    41.89752   

  DeathLocLong  
0    72.924161  
1    72.924161  
2    73.408713  
3    72.591985  
4    71.962064  

[5 rows x 36 columns]

In [4]:
results_df.columns

Index(['CaseNumber', 'Date', 'Year', 'Sex', 'Race', 'Age', 'Residence City',
       'Residence State', 'Residence County', 'Death City', 'Death State',
       'Death County', 'Location', 'DescriptionofInjury', 'InjuryPlace',
       'ImmediateCauseA', 'Heroin', 'Cocaine', 'Fentanyl', 'Oxycodone',
       'Oxymorphone', 'EtOH', 'Hydrocodone', 'Benzodiazepine', 'Methadone',
       'Amphet', 'Tramad', 'Morphine (not heroin)', 'Other', 'Any Opioid',
       'MannerofDeath', 'AmendedMannerofDeath', 'DeathLoc',
       'DeathLocationCity', 'DeathLocLat', 'DeathLocLong'],
      dtype='object')

In [5]:
target_url = f"https://maps.googleapis.com/maps/api/geocode/json?" \
            f"address=Hartford,CT,USA&key={gkey}"
try:
    geo_data = requests.get(target_url).json() 
    CT_lat = geo_data["results"][0]["geometry"]["location"]["lat"]
    CT_lng = geo_data["results"][0]["geometry"]["location"]["lng"]
except Exception as exp:
    print ("Cannot find geocode for Hartford: ", exp)

In [6]:
death_counts = Counter(results_df["Death County"])
death_counts

Counter({'New Haven': 1135,
         'Litchfield': 215,
         'Hartford': 1238,
         'Windham': 151,
         'Middlesex': 176,
         'Fairfield': 668,
         'New London': 381,
         'Tolland': 115})

In [7]:
df = pd.DataFrame.from_dict(death_counts, orient='index').reset_index()
df = df.rename(columns={'index':'County',0:'Num Deaths'})
df

County  Num Deaths
0   New Haven        1135
1  Litchfield         215
2    Hartford        1238
3     Windham         151
4   Middlesex         176
5   Fairfield         668
6  New London         381
7     Tolland         115

In [8]:
state_geo = "../Resources/tl_2010_09_county10.json"
json_data=open(state_geo).read()

jdata = json.loads(json_data)
# pprint(jdata.keys())
#pprint(jdata['features'][0]['properties'])

pprint([d['properties']['NAME10'] for d in jdata['features'] ])

['Fairfield',
 'New London',
 'Litchfield',
 'Windham',
 'Tolland',
 'Hartford',
 'Middlesex',
 'New Haven']


In [9]:
fmap = folium.Map([CT_lat, CT_lng], zoom_start=8,control_scale = True,tiles="Mapbox Bright")
fmap.choropleth(
 geo_data=state_geo,
 name='choropleth',
 data=df,
 columns=['County','Num Deaths'],
 key_on='feature.properties.NAME10',
 fill_color='PuRd',
 fill_opacity=0.7,
 line_opacity=0.2,
 legend_name='Drug Mortality'
)
folium.LayerControl().add_to(fmap)
 
# Save to html
fmap.save('county_choropleth.html')
fmap
# Image("county_choropleth_folium.jpg")

1. http://census.ire.org/data/bulkdata.html
2. http://mapshaper.org/
3. https://stackoverflow.com/questions/17267248/how-where-do-i-get-geojson-data-for-states-provinces-and-administrative-region

In [10]:
population = {'Fairfield':916829, 'New London':274055,'Litchfield':189927,
                                         'Windham': 118428,'Tolland':152691,'Hartford':894014,
                                         'Middlesex':165676,'New Haven': 862477}
df["Population"]= df['County'].map(population)
df['Normalized Death to 100,000'] = df["Num Deaths"]/df["Population"] *100000
df

County  Num Deaths  Population  Normalized Death to 100,000
0   New Haven        1135      862477                   131.597712
1  Litchfield         215      189927                   113.201388
2    Hartford        1238      894014                   138.476579
3     Windham         151      118428                   127.503631
4   Middlesex         176      165676                   106.231440
5   Fairfield         668      916829                    72.859824
6  New London         381      274055                   139.023189
7     Tolland         115      152691                    75.315506

In [11]:
state_geo = "../Resources/tl_2010_09_county10.json"

In [12]:
fmap_norm = folium.Map([CT_lat, CT_lng], zoom_start=8,control_scale = True,tiles="Mapbox Bright")
fmap_norm.choropleth(
 geo_data=state_geo,
 name='choropleth',
 data=df,
 columns=['County','Normalized Death to 100,000'],
 key_on='feature.properties.NAME10',
 fill_color='PuRd',
 fill_opacity=0.7,
 line_opacity=0.2,
 legend_name='Normalized Drug Mortality to 100,000'
)
folium.LayerControl().add_to(fmap_norm)
 
# Save to html
fmap_norm.save('county_choropleth_norm.html')
fmap_norm

In [13]:
results_df["Death City"] = results_df["Death City"].str.title() 
town_death_counts = Counter(results_df["Death City"])
town_death_counts.most_common()

[('Hartford', 427),
 ('New Haven', 303),
 ('Waterbury', 283),
 ('Bridgeport', 271),
 ('New Britain', 169),
 ('Norwich', 124),
 ('Meriden', 120),
 ('Bristol', 117),
 ('Danbury', 111),
 ('New London', 110),
 ('Torrington', 88),
 ('Middletown', 82),
 ('Manchester', 79),
 ('Enfield', 68),
 ('West Haven', 60),
 ('Stamford', 60),
 ('Milford', 59),
 ('Norwalk', 56),
 ('East Hartford', 54),
 ('Derby', 53),
 ('Southington', 49),
 ('Willimantic', 43),
 ('Stratford', 43),
 ('Vernon', 39),
 ('Hamden', 38),
 ('New Milford', 35),
 ('Groton', 33),
 ('Naugatuck', 33),
 ('Wallingford', 31),
 ('Branford', 26),
 ('Putnam', 23),
 ('East Haven', 23),
 ('West Hartford', 23),
 ('Wethersfield', 23),
 ('Shelton', 22),
 ('Newington', 22),
 ('Greenwich', 20),
 ('Ansonia', 20),
 ('Windsor', 19),
 ('Farmington', 18),
 ('Glastonbury', 18),
 ('Plainville', 17),
 ('Berlin', 17),
 ('Windsor Locks', 17),
 ('Plainfield', 15),
 ('Clinton', 14),
 ('North Haven', 14),
 ('Sharon', 13),
 ('Trumbull', 13),
 ('East Hampton', 1

In [15]:
town_df = pd.DataFrame.from_dict(town_death_counts, orient='index').reset_index()
town_df = town_df.rename(columns={'index':'Town',0:'Num Deaths'})
town_df.head()

Town  Num Deaths
0    New Haven         303
1  New Milford          35
2      Enfield          68
3      Pomfret           1
4   Middletown          82

In [16]:
town_geo = "../Resources/townct_37800_0000_2010_s100_census_1_shp_wgs84.json"
with open(town_geo) as f:
    town_struct = json.load(f)
town_struct["features"][1]['properties']['NAME10']


'Bethel'

In [17]:
fmap_town = folium.Map([CT_lat, CT_lng], zoom_start=8,control_scale = True,tiles="Mapbox Bright")
fmap_town.choropleth(
 geo_data=town_geo,
 name='choropleth',
 data=town_df,
 columns=['Town','Num Deaths'],
 key_on='feature.properties.NAME10',
 fill_color='PuRd',
 fill_opacity=0.7,
 line_opacity=0.2,
 legend_name='Number of deaths in each city'
)
folium.LayerControl().add_to(fmap_town)
 
# Save to html
#fmap_norm.save('county_choropleth_norm.html')
fmap_town

In [18]:
city_classification_df = pd.read_csv("../Resources/urban_classification_CT.csv",encoding = "ISO-8859-1", 
                                     error_bad_lines=False, dtype='str').dropna(subset=["NAME"])
city_classification_df["NAME"] = city_classification_df["NAME"].str.split(",", expand=True)
city_classification_df["LSADC"] = city_classification_df["LSADC"].apply(str).map({'75': "Urban", '76': "Urban"})
city = []
classification = []
population = []
for i, row in city_classification_df.iterrows():
    for fd in row["NAME"].split("--"):
        city.append(fd)
        classification.append(row["LSADC"])   
city_classification = pd.Series(classification, index=city)        

In [19]:
area_type_deaths = pd.DataFrame.from_dict(town_death_counts, orient="index")
area_type_deaths["classification"] = city_classification
area_type_deaths = area_type_deaths.fillna({"classification":"Rural"})
area_type_deaths = area_type_deaths.rename(columns={0:"Number of Deaths"})
area_type_deaths.head()

Number of Deaths classification
New Haven                 303          Urban
New Milford                35          Rural
Enfield                    68          Rural
Pomfret                     1          Rural
Middletown                 82          Rural

In [20]:
area_total_deaths_df = area_type_deaths.groupby("classification").sum()

total_deaths = area_total_deaths_df["Number of Deaths"].sum()
total_deaths

4079

In [21]:
# From Census
area_total_deaths_df["Population Ratio"] = ["12","88"]

area_total_deaths_df["Expected Deaths"] = np.array([12,88])*total_deaths/100

area_total_deaths_df

Number of Deaths Population Ratio  Expected Deaths
classification                                                    
Rural                       2217               12           489.48
Urban                       1862               88          3589.52